In [69]:
# Cargo todas las librerías
# from matplotlib import pyplot as plt
from scipy import stats
import numpy as np

import pandas as pd
import plotly.express as px
import streamlit as st

In [70]:
# Cargo los archivos de datos en diferentes DataFrames
df_raw = pd.read_csv('/Users/Jesus/Code/vehicles/vehicles_us.csv')

## Descripción de los datos

In [71]:
df_raw.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 51525 entries, 0 to 51524
Data columns (total 13 columns):
 #   Column        Non-Null Count  Dtype  
---  ------        --------------  -----  
 0   price         51525 non-null  int64  
 1   model_year    47906 non-null  float64
 2   model         51525 non-null  object 
 3   condition     51525 non-null  object 
 4   cylinders     46265 non-null  float64
 5   fuel          51525 non-null  object 
 6   odometer      43633 non-null  float64
 7   transmission  51525 non-null  object 
 8   type          51525 non-null  object 
 9   paint_color   42258 non-null  object 
 10  is_4wd        25572 non-null  float64
 11  date_posted   51525 non-null  object 
 12  days_listed   51525 non-null  int64  
dtypes: float64(4), int64(2), object(7)
memory usage: 5.1+ MB


In [72]:
df_raw.head()

price  model_year           model  condition  cylinders fuel  odometer  \
0   9400      2011.0          bmw x5       good        6.0  gas  145000.0   
1  25500         NaN      ford f-150       good        6.0  gas   88705.0   
2   5500      2013.0  hyundai sonata   like new        4.0  gas  110000.0   
3   1500      2003.0      ford f-150       fair        8.0  gas       NaN   
4  14900      2017.0    chrysler 200  excellent        4.0  gas   80903.0   

  transmission    type paint_color  is_4wd date_posted  days_listed  
0    automatic     SUV         NaN     1.0  2018-06-23           19  
1    automatic  pickup       white     1.0  2018-10-19           50  
2    automatic   sedan         red     NaN  2019-02-07           79  
3    automatic  pickup         NaN     NaN  2019-03-22            9  
4    automatic   sedan       black     NaN  2019-04-02           28

In [73]:
df_raw.describe()

price    model_year     cylinders       odometer   is_4wd  \
count   51525.000000  47906.000000  46265.000000   43633.000000  25572.0   
mean    12132.464920   2009.750470      6.125235  115553.461738      1.0   
std     10040.803015      6.282065      1.660360   65094.611341      0.0   
min         1.000000   1908.000000      3.000000       0.000000      1.0   
25%      5000.000000   2006.000000      4.000000   70000.000000      1.0   
50%      9000.000000   2011.000000      6.000000  113000.000000      1.0   
75%     16839.000000   2014.000000      8.000000  155000.000000      1.0   
max    375000.000000   2019.000000     12.000000  990000.000000      1.0   

       days_listed  
count  51525.00000  
mean      39.55476  
std       28.20427  
min        0.00000  
25%       19.00000  
50%       33.00000  
75%       53.00000  
max      271.00000

In [74]:
df_raw.describe(include='object')

model  condition   fuel transmission   type paint_color  \
count        51525      51525  51525        51525  51525       42258   
unique         100          6      5            3     13          12   
top     ford f-150  excellent    gas    automatic    SUV       white   
freq          2796      24773  47288        46902  12405       10029   

       date_posted  
count        51525  
unique         354  
top     2019-03-17  
freq           186

## Tratamiento:

In [75]:
df_sin_na = df_raw

# Funcion que analiza y muestra la cantidad con porcentaje de valores ausentes por columna.
def analizar_valores_ausentes(df, nombre_df='el_DataFrame'):
    # Parámetros: ( df= DataFrame a analizar, nombre_df= Nombre del DataFrame )

    # Calculo el total de filas
    total_filas = df.shape[0]

    # Obtengo el conteo de valores ausentes por columna
    valores_ausentes = df.isna().sum()

    print(f"Análisis de valores ausentes en {nombre_df}:")
    print("")

    # Recorrer cada columna y mostrar resultados
    for columna, na_count in valores_ausentes.items():
        if na_count > 0:  # Solo mostrar columnas con valores ausentes
            porcentaje = (na_count / total_filas) * 100
            print(f"Identifiqué {na_count} valores ausentes en la columna '{columna}' "
                  f"({porcentaje:.2f}% del total).")

    print(f"\nColumnas con valores ausentes: {sum(valores_ausentes > 0)} de {len(df.columns)}")

analizar_valores_ausentes(df_sin_na, 'vehiculos')

Análisis de valores ausentes en vehiculos:

Identifiqué 3619 valores ausentes en la columna 'model_year' (7.02% del total).
Identifiqué 5260 valores ausentes en la columna 'cylinders' (10.21% del total).
Identifiqué 7892 valores ausentes en la columna 'odometer' (15.32% del total).
Identifiqué 9267 valores ausentes en la columna 'paint_color' (17.99% del total).
Identifiqué 25953 valores ausentes en la columna 'is_4wd' (50.37% del total).

Columnas con valores ausentes: 5 de 13


In [76]:
df_sin_na = df_raw

# Elimine los ausentes de las columnas
df_sin_na.dropna(subset=['model_year','cylinders','odometer'], inplace=True)

# Reempplazo los ausentes de las columnas
df_sin_na.fillna({'paint_color':'Unknown'}, inplace=True)
df_sin_na.fillna({'is_4wd':0}, inplace=True)


In [77]:
# Busqueda de filas duplicadas
df_sin_na.duplicated().sum()

np.int64(0)

In [78]:
# Trasfomacion de columnas
df_transformado = df_sin_na
df_transformado['model_year'] = df_transformado['model_year'].astype('int')
df_transformado['cylinders'] = df_transformado['cylinders'].astype('int')
df_transformado['is_4wd'] = df_transformado['is_4wd'].astype('bool')

# Creo la columna de fabricante al extraer la primera palabra de modelo
df_transformado['manufacturer'] = df_transformado['model'].str.split().str[0]

df_car = df_transformado.reset_index()

## Pasos

In [92]:
df_car.head()
df_car.columns

Index(['index', 'price', 'model_year', 'model', 'condition', 'cylinders',
       'fuel', 'odometer', 'transmission', 'type', 'paint_color', 'is_4wd',
       'date_posted', 'days_listed', 'manufacturer'],
      dtype='object')

In [81]:
fig = px.histogram(df_car, x="model_year", color='condition') # crear un histograma
fig.show() # crear gráfico de dispersión

In [87]:
fig = px.histogram(df_car, x='model_year', color='condition') # crear un histograma
fig.show() # crear gráfico de dispersión
fig = px.box(df_car, x='model_year', y='condition', color='condition')
fig.show()

In [ ]:
fig = px.histogram(df_car, x='price', color='type') # crear un histograma
fig.show() # crear gráfico de dispersión
fig = px.box(df_car, x='price', y='type', color='type')
fig.show()

In [86]:
fig = px.histogram(df_car, x='days_listed', color='type') # crear un histograma
fig.show() # crear gráfico de dispersión
fig = px.box(df_car, x='days_listed', y='type', color='type')
fig.show()

In [90]:
fig = px.scatter(df_car, x="odometer", y="price") # crear un gráfico de dispersión
fig.show() # crear gráfico de dispersión

# Paso 4. Desarrollo del cuadro de mandos de la aplicación web

Al menos un encabezado (puedes utilizar st.header() para hacerlo.

In [56]:

fig = px.bar(car_data, x='manufacturer', color='type')
fig.show()

In [ ]:
['index', 'price', 'model_year', 'model', 'condition', 'cylinders',
       'fuel', 'odometer', 'transmission', 'type', 'paint_color', 'is_4wd',
       'date_posted', 'days_listed', 'manufacturer']

In [ ]:
opcion_disponible = ['price', 'model_year', 'condition',
       'odometer','type', 'paint_color', 'is_4wd',
       'date_posted', 'days_listed', 'manufacturer']
opcion_a = st.selectbox('Elije una opcion', opcion_disponible)

In [ ]:
#------------------------------------------------------------------------------#
#-GRAFICO DE BARRAS INTERACTIVO------------------------------------------------#
#------------------------------------------------------------------------------# 
st.subheader('Comparación por tipos de vehículos:')

# Opciones para ejes X e Y (numéricas o categóricas)
opcion_disponible = [
    ('price', 'Precio'),
    ('model_year', 'Año del modelo'),
    ('odometer', 'Kilometraje'),
    ('paint_color', 'Color'),
    ('is_4wd', 'Tracción 4x4'),
    ('date_posted', 'Fecha de publicación'),
    ('days_listed', 'Días en lista'),
    ('manufacturer', 'Fabricante'),
    ('condition', 'Condición'),
    ('fuel', 'Combustible'),
    ('transmission', 'Transmisión'),
    ('type', 'Tipo de vehículo'),
    ('paint_color', 'Color de la pintura'),
    ('manufacturer', 'Fabricante')
]

opcion_disponible_y = [
    ('price', 'Precio'),
    ('model_year', 'Año del modelo'),
    ('odometer', 'Kilometraje'),
    ('paint_color', 'Color'),
    ('is_4wd', 'Tracción 4x4'),
    ('date_posted', 'Fecha de publicación'),
    ('days_listed', 'Días en lista'),
    ('manufacturer', 'Fabricante')
]

opcion_x = st.selectbox(
    'Elige una opción para el eje X:',
    opcion_disponible,
    format_func=lambda x: x[1],
    key='x_axis'
)

opcion_y = st.selectbox(
    'Elige una opción para el eje Y:',
    opcion_disponible_y,
    format_func=lambda x: x[1],
    key='y_axis'
)

# Opción categórica para el color (siempre visible)
opcion_categorica = [
    ('condition', 'Condición'),
    ('fuel', 'Combustible'),
    ('transmission', 'Transmisión'),
    ('type', 'Tipo de vehículo'),
    ('paint_color', 'Color de la pintura'),
    ('manufacturer', 'Fabricante')
]

opcion_c = st.selectbox(
    'Elige una categoría para el color (opcional):',
    opcion_categorica,
    format_func=lambda x: x[1],
)

# Checkbox para aplicar o no la categorización (después de la lista)
usar_categoria = st.checkbox("Aplicar color por categoría seleccionada", value=False)  # Desactivado por defecto

# Crear el gráfico con o sin categorización
if usar_categoria:
    fig = px.histogram(
        df_car, 
        x=opcion_x[0],  
        y=opcion_y[0],  
        color=opcion_c[0],  # Aplica color si el checkbox está activado
        title=f"{opcion_y[1]} vs {opcion_x[1]} (coloreado por {opcion_c[1]})"
    )
else:
    fig = px.histogram(
        df_car, 
        x=opcion_x[0],  
        y=opcion_y[0],  
        title=f"{opcion_y[1]} vs {opcion_x[1]}"
    )

# Mostrar el gráfico
st.plotly_chart(fig, use_container_width=True)
#------------------------------------------------------------------------------#

In [ ]:
#################################################################################

st.subheader("Gráfico de Dispersión Interactivo 🚗")

# --- Casilla de verificación en lugar de botón ---
mostrar_grafico = st.checkbox('Mostrar gráfico de dispersión', value=False)

# Si la casilla está marcada, mostrar el gráfico
if mostrar_grafico:
    st.write('Visualización del gráfico de dispersión para el conjunto de datos de anuncios de venta de coches')
    
    # Crear el gráfico
    fig = px.scatter(
        df_filtered,
        x='model_year',
        y=opcion_y[0],    
        title="Relación Precio vs. Kilometraje",
        labels={"odometer": "Kilómetros recorridos", "price": "Precio (USD)"},
        hover_name="model"  # Opcional: muestra el modelo al pasar el cursor
    )
    
    # Mostrar el gráfico
    st.plotly_chart(fig, use_container_width=True)
else:
    st.write("Marca la casilla para ver el gráfico.")  # Mensaje si no está activado
     

NameError: name 'st' is not defined